# Exercise: Geographical Cluster Analysis of Taxi Rides
Using the NY Taxi data set (see Use Case Block I) and the use case from the lecture...

In [1]:
import pandas as pd
import numpy as np
import folium


In [2]:
# we load the data we have saved after wrangling and pre-processing in block I
train=pd.read_csv('../../DATA/train_cleaned.csv')

In [3]:
#select only the culumns with the ride coordinates
coordinates = train[ ['pickup_latitude','pickup_longitude','dropoff_latitude' , 'dropoff_longitude' ] ]

## Clustering approach from the lecture
we will be using simple K-Means:
https://scikit-learn.org/stable/modules/generated/sklearn.cluster.KMeans.html

In [4]:
from sklearn.cluster import KMeans

In [5]:
#define number of clusters and create instance
clusters=100
myKMeans=KMeans(n_clusters=clusters, n_jobs=-1)#parallelize to all cores

In [15]:
%%time
#train model
myKMeans.fit(coordinates.to_numpy()[:100000,:])#use only subset of the data to make it faster

C:\Users\Standard\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:938: FutureWarning: 'n_jobs' was deprecated in version 0.23 and will be removed in 0.25.
  warnings.warn("'n_jobs' was deprecated in version 0.23 and will be"


Wall time: 1min 37s


KMeans(n_clusters=100, n_jobs=-1)

In [14]:
#get cluster centers
centers=myKMeans.cluster_centers_

In [11]:
#draw map: green: start, red: end
cluster_map = folium.Map(location = [40.730610,-73.935242],zoom_start = 12,)
for i in range(clusters):
    folium.CircleMarker([centers[i,0], centers[i,1]], radius=3,                
                        color="green", 
                        fill_opacity=0.9
                       ).add_to(cluster_map)
    folium.CircleMarker([centers[i,2], centers[i,3]], radius=3,                
                        color="red", 
                        fill_opacity=0.9
                       ).add_to(cluster_map)
    folium.PolyLine([ [centers[i,0],centers[i,1]] , [centers[i,2],centers[i,3]]  ], color="black", weight=2.5, opacity=1).add_to(cluster_map)

In [12]:
cluster_map

## Exercise 1
Write a function ```show_cluster(cluster_number,...)``` that draws the cluster centers and all start and end points of a given cluster in the map.
* use the ```predict()``` method to map all data in ```train_data``` to a cluster center
* use ```folium.CircleMarker``` to draw all members of a given cluster


In [105]:
def show_cluster(cluster_number, train_data, coordinates):
    # Get classification of samples
    train_predict = train_data.predict(coordinates.to_numpy()[:100000,:])
    
    # Filter array to only have the index equal to cluster number
    cluster_index = np.where(train_predict == cluster_number)
    
    # Show circles
    cluster_map = folium.Map(location = [40.730610,-73.935242],zoom_start = 12,)
    for i in np.nditer(cluster_index):
        folium.CircleMarker([coordinates.loc[i].pickup_latitude, coordinates.loc[i].pickup_longitude], radius=3,                
                            color="green", 
                            fill_opacity=0.9
                            ).add_to(cluster_map)
        folium.CircleMarker([coordinates.loc[i].dropoff_latitude, coordinates.loc[i].dropoff_longitude], radius=3,                
                            color="red", 
                            fill_opacity=0.9
                            ).add_to(cluster_map)
    return cluster_map

In [117]:
show_cluster(1, myKMeans, coordinates)

## Exercise 2
Write a function ```cluster_var(cluster_number,...)``` that computes the intra- and extra cluster variance for a given cluster. Apply it to all clusters and compare the results for k=100 and k=10.

In [110]:
from sklearn import metrics

In [115]:
def cluster_var(cluster_number, train_data):
        metrics.calinski_harabasz_score(train_data, train_data.labels_)

In [119]:
myKMeans
#cluster_var(1, myKMeans)

KMeans(n_clusters=100, n_jobs=-1)

In [125]:
hey = coordinates[:100000,:]

TypeError: '(slice(None, 100000, None), slice(None, None, None))' is an invalid key

In [123]:
hey["Cluster_ID"]=myKMeans.labels_

ValueError: Length of values (100000) does not match length of index (400000)

In [124]:
hey.shape

(400000, 4)